# Лабораторная работа №3

## Набор данных Students Performance in Exams (Успеваемость студентов на экзаменах)

Выгрузка данных из CSV файла в датафрейм

In [674]:
import pandas as pd
import numpy as np
from sklearn import set_config

set_config(transform_output="pandas")

random_state=9
# Загрузка данных
df = pd.read_csv("..//..//static//csv//StudentsPerformance.csv")


### Описание набора  

Контекст
Оценки, полученные студентами

Содержание
Этот набор данных состоит из оценок, полученных учащимися по различным предметам.

Вдохновение
Понять влияние происхождения родителей, подготовки к тестированию и т. д. на успеваемость учащихся.

### Анализ содержимого

*Объекты наблюдения:* студенты, участвующие в экзаменах.

*Атрибуты объектов:* 

1. gender — пол: определяет гендерную принадлежность студента (мужской, женский).  
2. race/ethnicity — этническая принадлежность: группа, к которой относится студент (например, различные расовые/этнические категории).  
3. parental level of education — уровень образования родителей(например, среднее образование, высшее образование и т.д.).  
4. lunch — тип обеда: информация о том, получает ли студент бесплатный или платный обед.  
5. test preparation course — курс подготовки к тесту
6. math score  — результаты экзаменов по математике.
7. reading score — результаты экзаменов по чтению.
8. writing score — результаты экзаменов по письму.


### Бизнес-цель:

**Цель**: Разработка модели, которая будет классифицировать студентов на основе их предсказанных баллов в одну из категорий: High, Medium, Low.  

**Эффект**: Это позволит образовательным учреждениям не только выявлять студентов с низкими результатами, но и более точно классифицировать их на разные группы. Например, те, кто попадает в группу "High", могут получить более сложные задания, а те, кто в группе "Low", могут потребовать дополнительной помощи.


### Техническая цель

**Цель**: Разработка классификационной модели, которая будет работать с целевым признаком "total_score_discrete", классифицируя студентов по трем категориям (High, Medium, Low).  

**Подход**: Для этой задачи можно использовать алгоритмы классификации, такие как логистическая регрессия, деревья решений или случайные леса. Модели должны учитывать категориальные переменные и их влияние на категориальный целевой признак. Методы переклассификации будут оценивать, в какую категорию попадает студент на основе его характеристик.


### Конструирование признаков для решения задач

Можно создать новый признак, который будет представлять общую успеваемость студента. Например, можно суммировать баллы по всем предметам и создать общий балл. 

Далее используем дискретизацию числового признака (преобразование баллов в категории) для обучения модели, которая будет работать с дискретными данными, а не с непрерывными.

Категории:

"Low", "Medium", "High" для баллов


In [675]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

# Создание новых признаков
# - Общий балл
df['total_score'] = df['math score'] + df['reading score'] + df['writing score']

# - Категоризация баллов по математике, чтению и письму
def discretize_score(score):
     if score < 200:
         return 0
     elif 200 <= score < 250:
         return 1
     else:
         return 2
df['total_score_discrete'] = df['total_score'].apply(lambda x: discretize_score(x))

df = df.drop(columns=['math score', 'reading score', 'writing score','total_score'])

#### Выберем три модели для задач классификации

1. Логистическая регрессия (Logistic Regression) — базовая модель для классификации.

2. Дерево решений (Decision Tree) — модель, которая хорошо справляется с выявлением сложных закономерностей.

3. Градиентный бустинг (Gradient Boosting) — мощная ансамблевая модель, обеспечивающая высокое качество предсказаний.

Модели выбраны исходя из того, что они предоставляют разные подходы к решению задачи, и это позволит сравнить эффективность различных методов.

#### Разделение набора данных на обучающую и тестовые выборки (80/20) для задачи классификации и создание ориентира

Целевой признак -- total_score_discrete

In [676]:
from utils import split_stratified_into_train_val_test

X_train, X_val, X_test, y_train, y_val, y_test = split_stratified_into_train_val_test(
    df, stratify_colname="total_score_discrete", frac_train=0.80, frac_val=0, frac_test=0.20, random_state=random_state
)

#### Аугментация данных для целевого признака в обучающей выборке

In [677]:
from imblearn.over_sampling import RandomOverSampler


print("Количество данных в y_train до RandomOverSampling:", len(y_train))
print("Количество данных в X_train до RandomOverSampling:", len(X_train))

# Объединяем исходные данные и "шумные" данные для увеличения обучающей выборки
X_train_combined = np.vstack([X_train, X_train])
y_train_combined = np.hstack([y_train, y_train])  # Убедитесь, что y_train повторяется для новых данных

# Применение oversampling и undersampling
ros = RandomOverSampler(random_state=42)
X_train, y_train = ros.fit_resample(X_train, y_train)


print("Количество данных в y_train после RandomOverSampling:", len(y_train))
print("Количество данных в X_train после RandomOverSampling:", len(X_train))


Количество данных в y_train до RandomOverSampling: 800
Количество данных в X_train до RandomOverSampling: 800
Количество данных в y_train после RandomOverSampling: 1065
Количество данных в X_train после RandomOverSampling: 1065


#### Формирование конвейера

In [678]:
from sklearn.compose import ColumnTransformer
from sklearn.discriminant_analysis import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder


columns_to_drop = ["total_score_discrete"]
num_columns = [
    column
    for column in df.columns
    if column not in columns_to_drop and df[column].dtype != "object"
]
cat_columns = [
    column
    for column in df.columns
    if column not in columns_to_drop and df[column].dtype == "object"
]

num_imputer = SimpleImputer(strategy="median")
num_scaler = StandardScaler()
preprocessing_num = Pipeline(
    [
        ("imputer", num_imputer),
        ("scaler", num_scaler),
    ]
)

cat_imputer = SimpleImputer(strategy="constant", fill_value="unknown")
cat_encoder = OneHotEncoder(handle_unknown="ignore", sparse_output=False, drop="first")
preprocessing_cat = Pipeline(
    [
        ("imputer", cat_imputer),
        ("encoder", cat_encoder),
    ]
)

features_preprocessing = ColumnTransformer(
    verbose_feature_names_out=False,
    transformers=[
        ("prepocessing_num", preprocessing_num, num_columns),
        ("prepocessing_cat", preprocessing_cat, cat_columns),
    ],
    remainder="passthrough",
    force_int_remainder_cols=False  
)

drop_columns = ColumnTransformer(
    verbose_feature_names_out=False,
    transformers=[
        ("drop_columns", "drop", columns_to_drop),
    ],
    remainder="passthrough",
)


#### Настройка гиперпараметров для каждой модели и обучение

Для каждой модели важно настроить гиперпараметры, чтобы достичь наилучших результатов. Мы будем использовать GridSearchCV для выполнения кросс-валидации и выбора оптимальных гиперпараметров для каждой модели.

##### 1. Логистическая регрессия
Для логистической регрессии мы настроим гиперпараметры регуляризации C и оптимизатор.

In [679]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

# Модель логистической регрессии
logistic_model = LogisticRegression(max_iter=1000, random_state=random_state)

# Создаём пайплайн, который сначала применяет preprocessing, а потом обучает модель
logistic_pipeline = Pipeline([
    ("features_preprocessing", features_preprocessing),
    ("drop_columns", drop_columns),
    ("model", logistic_model)  # Здесь добавляем модель в пайплайн
])

# Параметры для настройки
logistic_param_grid = {
    'model__C': [0.1, 1, 10],  # Регуляризация
    'model__solver': ['liblinear', 'saga']  # Алгоритм оптимизации
}

# Настройка гиперпараметров с использованием GridSearchCV
logistic_search = GridSearchCV(logistic_pipeline, logistic_param_grid, cv=5, n_jobs=-1)

# Обучаем модель
logistic_search.fit(X_train, y_train.values.ravel())


d:\5semestr\AIM\aimvenv\Lib\site-packages\sklearn\compose\_column_transformer.py:1623: FutureWarning: 
The format of the columns of the 'remainder' transformer in ColumnTransformer.transformers_ will change in version 1.7 to match the format of the other transformers.
At the moment the remainder columns are stored as indices (of type int). With the same ColumnTransformer configuration, in the future they will be stored as column names (of type str).
To use the new behavior now and suppress this warning, use ColumnTransformer(force_int_remainder_cols=False).

  warnings.warn(


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('features_preprocessing',
                                        ColumnTransformer(force_int_remainder_cols=False,
                                                          remainder='passthrough',
                                                          transformers=[('prepocessing_num',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('scaler',
                                                                                          StandardScaler())]),
                                                                         []),
                                                                        ('prepocessing_cat',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(fill_value='unkno...
                                                                          'preparation '
                                                                          'course'])],
                                                          verbose_feature_names_out=False)),
                                       ('drop_columns',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('drop_columns',
                                                                         'drop',
                                                                         ['total_score_discrete'])],
                                                          verbose_feature_names_out=False)),
                                       ('model',
                                        LogisticRegression(max_iter=1000,
                                                           random_state=9))]),
             n_jobs=-1,
             param_grid={'model__C': [0.1, 1, 10],
                         'model__solver': ['liblinear', 'saga']})

##### 2. Дерево решений

Для дерева решений мы будем настраивать гиперпараметры, такие как максимальная глубина и минимальное количество объектов для разделения.


In [680]:
from sklearn.tree import DecisionTreeClassifier

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

# Модель дерева решений
decision_tree_model = DecisionTreeClassifier(random_state=random_state)

# Создаём пайплайн, который сначала применяет preprocessing, а потом обучает модель
decision_tree_pipeline = Pipeline([
    ("features_preprocessing", features_preprocessing),
    ("drop_columns", drop_columns),
    ("model", decision_tree_model)  # Здесь добавляем модель в пайплайн
])

# Параметры для настройки
tree_param_grid = {
    'model__max_depth': [5, 10, None],  # Глубина дерева
    'model__min_samples_split': [2, 5, 10],  # Минимальное количество объектов для разделения
    'model__min_samples_leaf': [1, 2, 4],  # Минимальное количество объектов в листе
}

tree_search = GridSearchCV(decision_tree_pipeline, tree_param_grid, cv=5, n_jobs=-1)

# Обучаем модель
tree_search.fit(X_train, y_train.values.ravel())


d:\5semestr\AIM\aimvenv\Lib\site-packages\sklearn\compose\_column_transformer.py:1623: FutureWarning: 
The format of the columns of the 'remainder' transformer in ColumnTransformer.transformers_ will change in version 1.7 to match the format of the other transformers.
At the moment the remainder columns are stored as indices (of type int). With the same ColumnTransformer configuration, in the future they will be stored as column names (of type str).
To use the new behavior now and suppress this warning, use ColumnTransformer(force_int_remainder_cols=False).

  warnings.warn(


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('features_preprocessing',
                                        ColumnTransformer(force_int_remainder_cols=False,
                                                          remainder='passthrough',
                                                          transformers=[('prepocessing_num',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('scaler',
                                                                                          StandardScaler())]),
                                                                         []),
                                                                        ('prepocessing_cat',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(fill_value='unkno...
                                                          verbose_feature_names_out=False)),
                                       ('drop_columns',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('drop_columns',
                                                                         'drop',
                                                                         ['total_score_discrete'])],
                                                          verbose_feature_names_out=False)),
                                       ('model',
                                        DecisionTreeClassifier(random_state=9))]),
             n_jobs=-1,
             param_grid={'model__max_depth': [5, 10, None],
                         'model__min_samples_leaf': [1, 2, 4],
                         'model__min_samples_split': [2, 5, 10]})

##### 3. Градиентный бустинг

Для градиентного бустинга будем настраивать параметры, такие как количество деревьев и скорость обучения.

In [681]:
from sklearn.ensemble import GradientBoostingClassifier

# Модель градиентного бустинга
gradient_boosting_model = GradientBoostingClassifier(random_state=random_state)

# Создаём пайплайн, который сначала применяет preprocessing, а потом обучает модель
gradient_boosting_pipeline = Pipeline([
    ("features_preprocessing", features_preprocessing),
    ("drop_columns", drop_columns),
    ("model", gradient_boosting_model)  # Здесь добавляем модель в пайплайн
])

# Параметры для настройки
gb_param_grid = {
    'model__n_estimators': [100, 200],  # Количество деревьев
    'model__learning_rate': [0.05, 0.1, 0.2],  # Темп обучения
    'model__max_depth': [3, 5],  # Глубина деревьев
}

gb_search = GridSearchCV(gradient_boosting_pipeline, gb_param_grid, cv=5, n_jobs=-1)

# Обучаем модель
gb_search.fit(X_train, y_train.values.ravel())


d:\5semestr\AIM\aimvenv\Lib\site-packages\sklearn\compose\_column_transformer.py:1623: FutureWarning: 
The format of the columns of the 'remainder' transformer in ColumnTransformer.transformers_ will change in version 1.7 to match the format of the other transformers.
At the moment the remainder columns are stored as indices (of type int). With the same ColumnTransformer configuration, in the future they will be stored as column names (of type str).
To use the new behavior now and suppress this warning, use ColumnTransformer(force_int_remainder_cols=False).

  warnings.warn(


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('features_preprocessing',
                                        ColumnTransformer(force_int_remainder_cols=False,
                                                          remainder='passthrough',
                                                          transformers=[('prepocessing_num',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(strategy='median')),
                                                                                         ('scaler',
                                                                                          StandardScaler())]),
                                                                         []),
                                                                        ('prepocessing_cat',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer(fill_value='unkno...
                                                          verbose_feature_names_out=False)),
                                       ('drop_columns',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('drop_columns',
                                                                         'drop',
                                                                         ['total_score_discrete'])],
                                                          verbose_feature_names_out=False)),
                                       ('model',
                                        GradientBoostingClassifier(random_state=9))]),
             n_jobs=-1,
             param_grid={'model__learning_rate': [0.05, 0.1, 0.2],
                         'model__max_depth': [3, 5],
                         'model__n_estimators': [100, 200]})

#### Оценка качества моделей

Для оценки качества моделей будем использовать следующие метрики:

Accuracy — это базовая метрика, которая подходит для сбалансированных данных. Она поможет понять, какой процент всех предсказаний был верным.

Precision и Recall — эти метрики важны, когда данные могут быть несбалансированными. Для многоклассовых задач важно использовать macro-average, что означает вычисление этих метрик для каждого класса и усреднение.

F1-Score — хорошая метрика для задач с несбалансированными классами, так как она учитывает и точность, и полноту. Это важно, если ложные положительные и ложные отрицательные ошибки одинаково важны.

ROC AUC — используется для оценки качества модели в контексте разделения классов, особенно если у нас есть вероятности для каждого класса. Это даст дополнительную информацию о том, насколько хорошо модель различает классы.

MCC — это особенно полезно для оценки качества модели в случае несбалансированных данных. Это метрика, которая дает более сбалансированное представление о том, как модель предсказывает все классы.

In [682]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, confusion_matrix, matthews_corrcoef

# Получаем предсказания
y_pred = logistic_search.predict(X_test)

# Оценка качества модели
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred, average='macro')  # Для многоклассовой задачи используем macro
recall = recall_score(y_test, y_pred, average='macro')
f1 = f1_score(y_test, y_pred, average='macro')
roc_auc = roc_auc_score(y_test, logistic_search.predict_proba(X_test), multi_class='ovr', average='macro')
mcc = matthews_corrcoef(y_test, y_pred)

# Матрица ошибок
conf_matrix = confusion_matrix(y_test, y_pred)

# Печать метрик
print(f"Accuracy: {accuracy:.4f}")
print(f"Precision (macro): {precision:.4f}")
print(f"Recall (macro): {recall:.4f}")
print(f"F1-Score (macro): {f1:.4f}")
print(f"ROC AUC (macro): {roc_auc:.4f}")
print(f"MCC: {mcc:.4f}")
print(f"Confusion Matrix:\n{conf_matrix}")


Accuracy: 0.4550
Precision (macro): 0.4669
Recall (macro): 0.5094
F1-Score (macro): 0.4323
ROC AUC (macro): 0.6811
MCC: 0.2188
Confusion Matrix:
[[51 12 26]
 [30 20 33]
 [ 3  5 20]]


In [683]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, confusion_matrix, matthews_corrcoef

# Получаем предсказания
y_pred = tree_search.predict(X_test)

# Оценка качества модели
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred, average='macro')  # Для многоклассовой задачи используем macro
recall = recall_score(y_test, y_pred, average='macro')
f1 = f1_score(y_test, y_pred, average='macro')
roc_auc = roc_auc_score(y_test, tree_search.predict_proba(X_test), multi_class='ovr', average='macro')
mcc = matthews_corrcoef(y_test, y_pred)

# Матрица ошибок
conf_matrix = confusion_matrix(y_test, y_pred)

# Печать метрик
print(f"Accuracy: {accuracy:.4f}")
print(f"Precision (macro): {precision:.4f}")
print(f"Recall (macro): {recall:.4f}")
print(f"F1-Score (macro): {f1:.4f}")
print(f"ROC AUC (macro): {roc_auc:.4f}")
print(f"MCC: {mcc:.4f}")
print(f"Confusion Matrix:\n{conf_matrix}")


Accuracy: 0.4050
Precision (macro): 0.3830
Recall (macro): 0.4010
F1-Score (macro): 0.3819
ROC AUC (macro): 0.5808
MCC: 0.0763
Confusion Matrix:
[[41 32 16]
 [30 29 24]
 [ 8  9 11]]


In [684]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, confusion_matrix, matthews_corrcoef

# Получаем предсказания
y_pred = gb_search.predict(X_test)

# Оценка качества модели
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred, average='macro')  # Для многоклассовой задачи используем macro
recall = recall_score(y_test, y_pred, average='macro')
f1 = f1_score(y_test, y_pred, average='macro')
roc_auc = roc_auc_score(y_test, gb_search.predict_proba(X_test), multi_class='ovr', average='macro')
mcc = matthews_corrcoef(y_test, y_pred)

# Матрица ошибок
conf_matrix = confusion_matrix(y_test, y_pred)

# Печать метрик
print(f"Accuracy: {accuracy:.4f}")
print(f"Precision (macro): {precision:.4f}")
print(f"Recall (macro): {recall:.4f}")
print(f"F1-Score (macro): {f1:.4f}")
print(f"ROC AUC (macro): {roc_auc:.4f}")
print(f"MCC: {mcc:.4f}")
print(f"Confusion Matrix:\n{conf_matrix}")


Accuracy: 0.4100
Precision (macro): 0.3873
Recall (macro): 0.3889
F1-Score (macro): 0.3783
ROC AUC (macro): 0.5806
MCC: 0.0895
Confusion Matrix:
[[42 30 17]
 [25 31 27]
 [ 7 12  9]]


Логистическая регрессия показывает наилучшие результаты по большинству метрик, включая точность, полноту, F1-Score и ROC AUC. Она также имеет лучший MCC, что говорит о лучшем качестве предсказаний с учетом всех классов. Хотя все модели показывают относительно низкие значения, логистическая регрессия явно выделяется среди других.

Лучшей моделью является логистическая регрессия на основе анализа метрик.

#### Оценка смещения и дисперсии лучшей модели (логистическая регрессия).

In [685]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold

# Кросс-валидация на обучающих данных
kf = KFold(n_splits=5, shuffle=True, random_state=random_state)
train_accuracies = cross_val_score(logistic_pipeline, X_train, y_train.values.ravel(), cv=kf, scoring="accuracy")

# Прогнозирование на обучающих и тестовых данных
logistic_pipeline.fit(X_train, y_train.values.ravel())
train_accuracy = accuracy_score(y_train, logistic_pipeline.predict(X_train))
test_accuracy = accuracy_score(y_test, logistic_pipeline.predict(X_test))

# Смещение (Bias)
bias = 1 - test_accuracy  # Ошибка на тестовой выборке

# Дисперсия (Variance)
variance = np.var(train_accuracies)  # Дисперсия на обучающей выборке

# Выводим результаты
print(f"Средняя точность на обучающих данных (кросс-валидация): {np.mean(train_accuracies)}")
print(f"Точность на обучающей выборке: {train_accuracy}")
print(f"Точность на тестовой выборке: {test_accuracy}")
print(f"Смещение (Bias): {bias}")
print(f"Дисперсия (Variance): {variance}")


Средняя точность на обучающих данных (кросс-валидация): 0.5023474178403756
Точность на обучающей выборке: 0.536150234741784
Точность на тестовой выборке: 0.47
Смещение (Bias): 0.53
Дисперсия (Variance): 0.000581895126628314


Оценка модели:  

Смещение высокое (Bias = 53%) — это указывает на недообучение модели. Модель не может хорошо предсказать целевой признак на тестовых данных, что означает, что она слишком простая для данного набора данных или её регуляризация слишком сильна.

Дисперсия низкая (Variance = 0.00058) — это также подтверждает, что модель не переобучена. Она не слишком чувствительна к изменениям в обучающих данных.